<img src="../images/logo.jpg" style="width:85px;height:85px;float:left" /><h1 style="position:relative;float:left;display:inline">Conditional GAN from Scratch</h1>

<a href='https://colab.research.google.com/github/zurutech/gans-from-theory-to-production/blob/master/2.%20GANs%20in%20Tensorflow/BONUS%20-%20Conditional%20GAN%20from%20scratch.ipynb'>
    <img align="left" src='https://cdn-images-1.medium.com/max/800/1*ZpNn76K98snC9vDiIJ6Ldw.jpeg'></img>
</a>

In [1]:
import matplotlib
import matplotlib.pyplot as plt
import tensorflow as tf
from IPython import display
import random
import pylab as pl

Define the dataset size and the 2 random normal distribution

In [2]:
dataset_shape = (2000, 1)
def sample_z1():
    return tf.random.normal(mean=10., shape=dataset_shape, stddev=0.1, dtype=tf.float32)
def sample_z2():
    return tf.random.normal(mean=20., shape=dataset_shape, stddev=0.2, dtype=tf.float32)

Define the labels for the two distributions

In [3]:
l1 = tf.zeros(shape=(dataset_shape[0],1), dtype=tf.float32)
l2 = tf.ones(shape=(dataset_shape[0],1), dtype=tf.float32)

In [4]:
# distribution 1
_ = plt.hist(sample_z1().numpy(), 100)

In [5]:
# distribution 2
_ = plt.hist(sample_z2().numpy(), 100)

Define the generator and discriminator functions: both networks accepts a "conditioning" parameter - the label.

In [6]:
def generator(input_shape, condition_shape):
    """generator network.
    Args:
        input_shape: the desired input shape
        condition_shape: the shape of the condition 
    Returns:
        G: The generator model
    """
    inputs = tf.keras.layers.Input(input_shape)
    condition_inputs = tf.keras.layers.Input(condition_shape)
    
    net = tf.keras.layers.Concatenate()([inputs, condition_inputs])
    net = tf.keras.layers.Dense(units=64, activation=tf.nn.elu, name="fc1")(net)
    net = tf.keras.layers.Dense(units=64, activation=tf.nn.elu, name="fc2")(net)
    net = tf.keras.layers.Dense(units=1, name="G")(net)
    G = tf.keras.Model(inputs=[inputs, condition_inputs], outputs=net)
    return G
    
def disciminator(input_shape, condition_shape):
    """discriminator network.
    Args:
        input_shape: the desired input shape
        condition_shape: the shape of the condition
    Returns:
        D: the discriminator model
    """
    inputs = tf.keras.layers.Input(input_shape)
    condition_inputs = tf.keras.layers.Input(condition_shape)
    
    net = tf.keras.layers.Concatenate()([inputs, condition_inputs])
    net = tf.keras.layers.Dense(units=32, activation=tf.nn.elu, name="fc1")(net)
    net = tf.keras.layers.Dense(units=1, name="D")(net)
    D = tf.keras.Model(inputs=[inputs, condition_inputs], outputs=net)
    return D

Define the generator and discriminator - together with the conditional inputs

In [7]:
input_shape = (1,)
condition_shape = (1,)

D = disciminator(input_shape, condition_shape)

latent_space_shape = (100,)
G = generator(latent_space_shape, condition_shape)

Define the discriminator loss

In [8]:
bce = tf.keras.losses.BinaryCrossentropy(from_logits=True)

d_loss = lambda real_output, generated_output: bce(tf.ones_like(real_output), real_output) + bce(tf.zeros_like(generated_output), generated_output)

Define the generator loss

In [9]:
g_loss = lambda generated_output: bce(tf.ones_like(generated_output), generated_output)

Define the train function

In [15]:
def train():
    # Define the optimizers and the train operations
    optimizer = tf.keras.optimizers.Adam(1e-5)
    
    @tf.function
    def train_step():
        for real_data, label  in [(sample_z1(), l1), (sample_z2(), l2)]:
            with tf.GradientTape(persistent=True) as tape:
                noise_vector = tf.random.normal(mean=0, stddev=1, shape=(real_data.shape[0], latent_space_shape[0]))
                # Sample from the Generator
                fake_data = G([noise_vector, label])
                # Compute the D loss
                d_fake_data = D([fake_data, label])
                d_real_data = D([real_data, label])
                d_loss_value = d_loss(generated_output=d_fake_data, real_output=d_real_data)
                # Compute the G loss
                g_loss_value = g_loss(generated_output=d_fake_data)
                tf.print(label[0], "G loss: ", g_loss_value, " D loss: ", d_loss_value)
            # Now that we comptuted the losses we can compute the gradient (using the tape)
            # and optimize the networks
            d_gradients = tape.gradient(d_loss_value, D.trainable_variables)
            g_gradients = tape.gradient(g_loss_value, G.trainable_variables)
            del tape
        
            optimizer.apply_gradients(zip(d_gradients, D.trainable_variables))
            optimizer.apply_gradients(zip(g_gradients, G.trainable_variables))
    
    for step in range(40000):
        train_step()
train()      

[0] G loss:  0.693421245  D loss:  1.38517785
[1] G loss:  0.69544965  D loss:  1.38611543
[0] G loss:  0.693718731  D loss:  1.38519764
[1] G loss:  0.695322454  D loss:  1.38611066
[0] G loss:  0.693564  D loss:  1.38520586
[1] G loss:  0.69508642  D loss:  1.38610935
[0] G loss:  0.693446219  D loss:  1.38516831
[1] G loss:  0.694925904  D loss:  1.38610208
[0] G loss:  0.693241537  D loss:  1.38524282
[1] G loss:  0.694757223  D loss:  1.3861022
[0] G loss:  0.693141818  D loss:  1.38519418
[1] G loss:  0.694571793  D loss:  1.38609481
[0] G loss:  0.692969441  D loss:  1.38523293
[1] G loss:  0.694397  D loss:  1.38611317
[0] G loss:  0.692850947  D loss:  1.38523746
[1] G loss:  0.694230795  D loss:  1.38611555
[0] G loss:  0.692795575  D loss:  1.38516045
[1] G loss:  0.694107711  D loss:  1.38609743
[0] G loss:  0.692639053  D loss:  1.38522601
[1] G loss:  0.693978369  D loss:  1.38610721
[0] G loss:  0.692499876  D loss:  1.38527501
[1] G loss:  0.693800211  D loss:  1.386105

[0] G loss:  0.694837093  D loss:  1.38530791
[1] G loss:  0.6948421  D loss:  1.38610959
[0] G loss:  0.694922864  D loss:  1.38525307
[1] G loss:  0.695038795  D loss:  1.38611317
[0] G loss:  0.694909811  D loss:  1.38525891
[1] G loss:  0.695195198  D loss:  1.38610399
[0] G loss:  0.69489783  D loss:  1.38525772
[1] G loss:  0.695405  D loss:  1.38611186
[0] G loss:  0.69483912  D loss:  1.38531232
[1] G loss:  0.695603788  D loss:  1.38611817
[0] G loss:  0.694906354  D loss:  1.38523173
[1] G loss:  0.695859849  D loss:  1.38611889
[0] G loss:  0.694896162  D loss:  1.38523746
[1] G loss:  0.696099043  D loss:  1.38610744
[0] G loss:  0.694840074  D loss:  1.38526893
[1] G loss:  0.696308911  D loss:  1.38611138
[0] G loss:  0.694776952  D loss:  1.38527846
[1] G loss:  0.69643259  D loss:  1.38611221
[0] G loss:  0.694774091  D loss:  1.38516581
[1] G loss:  0.696461082  D loss:  1.38612747
[0] G loss:  0.694528  D loss:  1.38525498
[1] G loss:  0.696430862  D loss:  1.38611746

[1] G loss:  0.691401601  D loss:  1.38613558
[0] G loss:  0.69082886  D loss:  1.38524175
[1] G loss:  0.691289663  D loss:  1.38611734
[0] G loss:  0.690902114  D loss:  1.38522398
[1] G loss:  0.691208422  D loss:  1.38611424
[0] G loss:  0.690931916  D loss:  1.38527966
[1] G loss:  0.691140831  D loss:  1.38612676
[0] G loss:  0.690973639  D loss:  1.38531542
[1] G loss:  0.691043377  D loss:  1.38612008
[0] G loss:  0.691068053  D loss:  1.38529062
[1] G loss:  0.690959573  D loss:  1.38609552
[0] G loss:  0.691128194  D loss:  1.38530707
[1] G loss:  0.690859  D loss:  1.38610744
[0] G loss:  0.691304266  D loss:  1.3852278
[1] G loss:  0.690784931  D loss:  1.38609028
[0] G loss:  0.691321552  D loss:  1.38526511
[1] G loss:  0.690651655  D loss:  1.38608074
[0] G loss:  0.691361368  D loss:  1.38529313
[1] G loss:  0.69054991  D loss:  1.38608479
[0] G loss:  0.691438615  D loss:  1.3853147
[1] G loss:  0.690509915  D loss:  1.38609076
[0] G loss:  0.691609621  D loss:  1.3852

[0] G loss:  0.69355613  D loss:  1.38530302
[1] G loss:  0.692851186  D loss:  1.38609719
[0] G loss:  0.69357866  D loss:  1.38529205
[1] G loss:  0.692812443  D loss:  1.38609338
[0] G loss:  0.693472922  D loss:  1.38537133
[1] G loss:  0.692762911  D loss:  1.38609505
[0] G loss:  0.6934973  D loss:  1.38535786
[1] G loss:  0.69278115  D loss:  1.38610649
[0] G loss:  0.693622947  D loss:  1.38527787
[1] G loss:  0.692909777  D loss:  1.3861059
[0] G loss:  0.693687379  D loss:  1.38531685
[1] G loss:  0.69316256  D loss:  1.38610554
[0] G loss:  0.693836927  D loss:  1.38530934
[1] G loss:  0.69345969  D loss:  1.38611257
[0] G loss:  0.693967164  D loss:  1.38534975
[1] G loss:  0.693799257  D loss:  1.38610744
[0] G loss:  0.694161236  D loss:  1.38529801
[1] G loss:  0.694080114  D loss:  1.38611293
[0] G loss:  0.694243848  D loss:  1.3853451
[1] G loss:  0.694367528  D loss:  1.38611615
[0] G loss:  0.694405794  D loss:  1.38529766
[1] G loss:  0.694633901  D loss:  1.386107

[1] G loss:  0.694821  D loss:  1.38612044
[0] G loss:  0.693755805  D loss:  1.38531351
[1] G loss:  0.694829226  D loss:  1.38613534
[0] G loss:  0.693769515  D loss:  1.38525343
[1] G loss:  0.694827616  D loss:  1.38612497
[0] G loss:  0.69358027  D loss:  1.3853749
[1] G loss:  0.694806755  D loss:  1.38612747
[0] G loss:  0.693565547  D loss:  1.38530767
[1] G loss:  0.694733858  D loss:  1.38611603
[0] G loss:  0.693489373  D loss:  1.38527799
[1] G loss:  0.694648683  D loss:  1.3861289
[0] G loss:  0.693406  D loss:  1.38527894
[1] G loss:  0.694601417  D loss:  1.38612664
[0] G loss:  0.6933285  D loss:  1.3852911
[1] G loss:  0.694609046  D loss:  1.38610876
[0] G loss:  0.693340361  D loss:  1.38524246
[1] G loss:  0.694619119  D loss:  1.38613105
[0] G loss:  0.693204641  D loss:  1.38534129
[1] G loss:  0.694612801  D loss:  1.38612723
[0] G loss:  0.693225145  D loss:  1.38525474
[1] G loss:  0.694511473  D loss:  1.38613915
[0] G loss:  0.693128049  D loss:  1.38525176


...

[1] G loss:  0.694781244  D loss:  1.38631189
[0] G loss:  0.694102943  D loss:  1.38630354
[1] G loss:  0.694805503  D loss:  1.38631082
[0] G loss:  0.693970561  D loss:  1.38630295
[1] G loss:  0.694632471  D loss:  1.3863101
[0] G loss:  0.693790674  D loss:  1.38630295
[1] G loss:  0.694425642  D loss:  1.38631094
[0] G loss:  0.693585396  D loss:  1.38630354
[1] G loss:  0.694143116  D loss:  1.38630962
[0] G loss:  0.693402946  D loss:  1.38630271
[1] G loss:  0.694033086  D loss:  1.38630986
[0] G loss:  0.693300724  D loss:  1.3863039
[1] G loss:  0.694008172  D loss:  1.3863101
[0] G loss:  0.693239927  D loss:  1.38630486
[1] G loss:  0.69402343  D loss:  1.38631058
[0] G loss:  0.693134129  D loss:  1.38630474
[1] G loss:  0.693802357  D loss:  1.38631
[0] G loss:  0.692945659  D loss:  1.38630557
[1] G loss:  0.69351393  D loss:  1.38631153
[0] G loss:  0.692754865  D loss:  1.38630557
[1] G loss:  0.693183124  D loss:  1.38631213
[0] G loss:  0.692558  D loss:  1.38630652

[1] G loss:  0.692336917  D loss:  1.38631368
[0] G loss:  0.69221127  D loss:  1.386307
[1] G loss:  0.692216873  D loss:  1.38631439
[0] G loss:  0.69218564  D loss:  1.38630581
[1] G loss:  0.692150533  D loss:  1.38631511
[0] G loss:  0.692190766  D loss:  1.38630533
[1] G loss:  0.692051  D loss:  1.3863132
[0] G loss:  0.692196429  D loss:  1.38630605
[1] G loss:  0.691955566  D loss:  1.38631344
[0] G loss:  0.692205  D loss:  1.38630438
[1] G loss:  0.69186151  D loss:  1.38631344
[0] G loss:  0.692220509  D loss:  1.38630462
[1] G loss:  0.69175005  D loss:  1.38631296
[0] G loss:  0.692261457  D loss:  1.38630462
[1] G loss:  0.691761315  D loss:  1.38631201
[0] G loss:  0.692355275  D loss:  1.38630366
[1] G loss:  0.691807032  D loss:  1.38631225
[0] G loss:  0.69242847  D loss:  1.3863039
[1] G loss:  0.691717148  D loss:  1.38630939
[0] G loss:  0.692473888  D loss:  1.38630247
[1] G loss:  0.691688836  D loss:  1.38630939
[0] G loss:  0.69257772  D loss:  1.38630414
[1] 

[0] G loss:  0.692807496  D loss:  1.38630295
[1] G loss:  0.692012131  D loss:  1.38630891
[0] G loss:  0.692903042  D loss:  1.38630438
[1] G loss:  0.69206053  D loss:  1.38630962
[0] G loss:  0.693029821  D loss:  1.3863039
[1] G loss:  0.69221741  D loss:  1.3863095
[0] G loss:  0.69318831  D loss:  1.38630402
[1] G loss:  0.69243145  D loss:  1.38631177
[0] G loss:  0.69338882  D loss:  1.38630593
[1] G loss:  0.692807674  D loss:  1.3863132
[0] G loss:  0.693659067  D loss:  1.38630509
[1] G loss:  0.693291605  D loss:  1.38631439
[0] G loss:  0.693919778  D loss:  1.38630688
[1] G loss:  0.693710744  D loss:  1.3863132
[0] G loss:  0.694078684  D loss:  1.38630688
[1] G loss:  0.693882644  D loss:  1.38631403
[0] G loss:  0.694098  D loss:  1.38630795
[1] G loss:  0.693844855  D loss:  1.38631439
[0] G loss:  0.694068849  D loss:  1.38630724
[1] G loss:  0.693864524  D loss:  1.38631558
[0] G loss:  0.694075227  D loss:  1.386307
[1] G loss:  0.693971276  D loss:  1.38631451
[0

[0] G loss:  0.69443357  D loss:  1.38630533
[1] G loss:  0.695121944  D loss:  1.38631308
[0] G loss:  0.694333434  D loss:  1.3863045
[1] G loss:  0.694976747  D loss:  1.38631105
[0] G loss:  0.694126308  D loss:  1.38630319
[1] G loss:  0.69474858  D loss:  1.38631022
[0] G loss:  0.693948269  D loss:  1.38630199
[1] G loss:  0.694658756  D loss:  1.38630962
[0] G loss:  0.693838537  D loss:  1.38630319
[1] G loss:  0.694686234  D loss:  1.38630891
[0] G loss:  0.693730772  D loss:  1.38630271
[1] G loss:  0.694590151  D loss:  1.38630772
[0] G loss:  0.693576753  D loss:  1.38630259
[1] G loss:  0.694480419  D loss:  1.38630807
[0] G loss:  0.693435788  D loss:  1.38630331
[1] G loss:  0.694342077  D loss:  1.38630939
[0] G loss:  0.693249702  D loss:  1.38630414
[1] G loss:  0.694085  D loss:  1.38631105
[0] G loss:  0.693024  D loss:  1.38630533
[1] G loss:  0.693710208  D loss:  1.38631082
[0] G loss:  0.692784131  D loss:  1.38630557
[1] G loss:  0.693392396  D loss:  1.386311

[0] G loss:  0.692263484  D loss:  1.38630795
[1] G loss:  0.692544  D loss:  1.3863163
[0] G loss:  0.69209522  D loss:  1.38630772
[1] G loss:  0.692199  D loss:  1.38631535


In [17]:
real_data = sample_z1()
noise_vector = tf.random.normal(mean=0, stddev=1, shape=(real_data.shape[0], latent_space_shape[0]))

In [19]:
sampled = tf.squeeze(G([noise_vector, l2]))

_ = plt.hist(sampled, 100, range=(2, 25))

In [20]:
sampled = tf.squeeze(G([noise_vector, l1]))

_ = plt.hist(sampled, 100, range=(2, 25))